# Module 5 Advanced GIS Applications

### Learning Objectives

This final module covers advanced GIS applications. Specifically it will address the creation of interactive maps using python in a jupyter notebook environment. The code for creating this map has been pre-written for you and is from the tutorial guides provided at https://automating-gis-processes.github.io/CSC18/lessons/L5/interactive-map-bokeh.html and https://automating-gis-processes.github.io/CSC18/lessons/L5/advanced-bokeh.html. The code was used as a part of Python GIS course organized by CSC Finalnd - IT Center for Science. The lecturer for the course and original writer of the code is Henrikki Tenkanen, the course was taught in 2018, the full course material can be found at https://automating-gis-processes.github.io/CSC18/index.html. This is only one example of how python can be used for advanced GIS applications; other applications can include individual and batch processing, and data extraction via APIs. The key learning objectives for this module are:

1. Examine python code and understand the basic processes outlined
2. Understand how the code works together in a GIS context
3. Investigate the output of the code to identfiy how the components are combined for mapping applications

### Key Data for this Module

This module requires the following data:

1. Kitchener_DA_Population_Python.zip (Contains: Kitchener_DA_Population.shp)
2. Kitchener_Collisions_Ptython.zip (Contains: Traffic_Collisions.shp)
3. Kitchener_Roads_Python.zip (Contains: Kitchener_Roads.shp)

These zip files contain similar data to what was used in the previous modules, however, it has been slightly modified for use in python. Make sure to store these data in a different folder from your other data.

### Importing Python Packages

The first aspect of all python scripts is to import the packages that will be used. This allows access to the functions of these packages which we will use for mapping.

The main packages used for this script are:

1. Geopandas
2. Bokeh
3. Pysal
4. Numpy

The errors caused by our import statements are due to missing packages for certain (unnecessary) components of Pysal.

In [2]:
import geopandas as gpd
from bokeh.plotting import figure
from bokeh.models import ColumnDataSource, HoverTool, LogColorMapper
from bokeh.palettes import Greens8
from bokeh.io import show, output_notebook
from pysal import viz

### Loading Data

Once we have imported all the necessary packages, we can start to read in our geospatial data. Because we are dealing with sets of single files we need to set an individual variable to each of our file paths and create variables for the different geopandas dataframes. Make sure that you change the file paths below to match your own computer.

In [3]:
# Load in our geospatial data
# Location of our point file
traffic_collisions = "D:/GISWorkshop_Communitech/python_data/Traffic_Collisions.shp"

# Loading the data using geopandas
collisions_pt = gpd.read_file(traffic_collisions)

# Location of our line file
kitchener_roads =  "D:/GISWorkshop_Communitech/python_data/Kitchener_Roads.shp"

# Loading the data using geopandas
road_ln = gpd.read_file(kitchener_roads)

# Location of our polygon file
kitchener_DA = "D:/GISWorkshop_Communitech/python_data/Kitchener_DA_Population.shp"

# Loading the data using geopandas
kitchener_poly = gpd.read_file(kitchener_DA)

### Data Projections

As discussed several times in this workshop, keeping consistent spatial projections is a key aspect of geospatial processing. Therefore, here we extract the projection from one layer and set the geometry from the other layers to match.

In [4]:
# Ensure that we have the same projection for all our data
CRS = kitchener_poly.crs

# Set other layers to match our primary projection
collisions_pt['geometry'] = collisions_pt['geometry'].to_crs(crs=CRS)
road_ln['geometry'] = road_ln['geometry'].to_crs(crs=CRS)

### Extracting Coordinates

The next two cells deal with extracting geospatial coordinates. The first cell creates a set of three functions, each function is built to work with a different type of vector geometry. The second cell applies these functions to calculate the coordinates for the different files. Functions are useful for applying the same process to multiple variables within a python environment

In [5]:
# Creating a function to get the coordinates of point data
def getPointCoords(row, geom, coord_type):
    if coord_type == 'x':
        return row[geom].x
    elif coord_type == 'y':
        return row[geom].y

# Creating a function to get the coordinates of line data
def getLineCoords(row, geom, coord_type):
    if coord_type == 'x':
        return list( row[geom].coords.xy[0] )
    elif coord_type == 'y':
        return list( row[geom].coords.xy[1] )

# Creating a function to get the coordinates of our polygon data
def getPolyCoords(row, geom, coord_type):

    # Parse the exterior of the coordinate
    exterior = row[geom].exterior

    if coord_type == 'x':
        # Get the x coordinates of the exterior
        return list( exterior.coords.xy[0] )
    elif coord_type == 'y':
        # Get the y coordinates of the exterior
        return list( exterior.coords.xy[1] )

In [6]:
# Calculate our x and y coordinates using the getPointCoords
collisions_pt['x'] = collisions_pt.apply(getPointCoords, geom='geometry', coord_type='x', axis=1)
collisions_pt['y'] = collisions_pt.apply(getPointCoords, geom='geometry', coord_type='y', axis=1)

# Calculate our x and y coordinates using the getLineCoords
road_ln['x'] = road_ln.apply(getLineCoords, geom='geometry', coord_type='x', axis=1)
road_ln['y'] = road_ln.apply(getLineCoords, geom='geometry', coord_type='y', axis=1)

# Calculate our x and y coordinates using the getPolyCoords
kitchener_poly['x'] = kitchener_poly.apply(getPolyCoords, geom='geometry', coord_type='x', axis=1)
kitchener_poly['y'] = kitchener_poly.apply(getPolyCoords, geom='geometry', coord_type='y', axis=1)

### Classifying Data

Once we have all the coordinates we need to classify our population data for Kitchener. Here we are using the Quantile divisions in the data, however, this could be customized for many different options. You could even calculate the breaks outside of python and just create a simple list containing the values.

In [7]:
# Classify our population into 5 classes using the Quanitle method
# Create a list of values based on the Quantiles
breaks = [0, 439, 515, 591, 860, 7032]

# Initialize the classifier and apply it
classifier = viz.mapclassify.User_Defined.make(bins=breaks)
classify_pop = kitchener_poly[['Population']].apply(classifier)

# Rename the classified column
classify_pop.columns = ['Population_Class_Quantile']

# Join it back to the polygon layer
kitchener_poly = kitchener_poly.join(classify_pop)

c:\users\funny\miniconda3\lib\site-packages\pysal\viz\mapclassify\classifiers.py:482: UserWarning: Deprecated (2.1.0): User_Defined is being renamed to UserDefined. User_Defined will be removed on 2020-01-31.
  warn(self.message)


Here we call the first ten entries of our dataset to check whether we have added the class values to the dataset. We can also see that the data set includes x and y coordinates. 

In [8]:
kitchener_poly.head(10)

DAUID    CDNAME    CCSNAME  Population  ORIG_FID  \
0  35300473  Waterloo  Kitchener         660         0   
1  35300701  Waterloo  Kitchener        1008         1   
2  35300702  Waterloo  Kitchener         541         2   
3  35300143  Waterloo  Kitchener         464         3   
4  35300144  Waterloo  Kitchener         586         4   
5  35300145  Waterloo  Kitchener         649         5   
6  35300146  Waterloo  Kitchener         555         6   
7  35300147  Waterloo  Kitchener         623         7   
8  35300148  Waterloo  Kitchener         694         8   
9  35300149  Waterloo  Kitchener         917         9   

                                            geometry  \
0  POLYGON ((549474.004 4805022.999, 549159.998 4...   
1  POLYGON ((539992.056 4809238.184, 540033.349 4...   
2  POLYGON ((540819.003 4808423.999, 540837.998 4...   
3  POLYGON ((540430.005 4809184.003, 540407.000 4...   
4  POLYGON ((540792.998 4809120.996, 540786.000 4...   
5  POLYGON ((541138.003 4809657.994, 541199.995 4...   
6  POLYGON ((541289.002 4809174.002, 541343.003 4...   
7  POLYGON ((541352.003 4809071.003, 541343.003 4...   
8  POLYGON ((541572.999 4808781.001, 541497.002 4...   
9  POLYGON ((541000.997 4809051.001, 541064.999 4...   

                                                   x  \
0  [549474.0037216209, 549159.9982561187, 548993....   
1  [539992.0559903013, 540033.3494620966, 540056....   
2  [540819.0034892856, 540837.9979776781, 540871....   
3  [540430.0046868733, 540406.9998110479, 540406....   
4  [540792.9981110763, 540786.0003357477, 540783....   
5  [541138.0031464747, 541199.9952840323, 541361....   
6  [541289.0016307213, 541343.0025793707, 541323....   
7  [541352.0034156175, 541343.0025793707, 541289....   
8  [541572.9992464606, 541497.0024956351, 541436....   
9  [541000.9971179594, 541064.9987669536, 541065....   

                                                   y  \
0  [4805022.998578291, 4804780.999986702, 4804652...   
1  [4809238.183755367, 4809184.750778578, 4809201...   
2  [4808423.999499622, 4808355.0035882285, 480824...   
3  [4809184.002968112, 4809168.005271451, 4809168...   
4  [4809120.99589351, 4809012.001352376, 4808997....   
5  [4809657.994321193, 4809540.00520038, 4809621....   
6  [4809174.002187756, 4809062.9936238965, 480904...   
7  [4809071.002935526, 4809062.9936238965, 480917...   
8  [4808781.001136229, 4808742.995967955, 4808864...   
9  [4809051.0005227085, 4808968.00582448, 4808968...   

   Population_Class_Quantile  
0                          4  
1                          5  
2                          3  
3                          2  
4                          3  
5                          4  
6                          3  
7                          4  
8                          4  
9                          5

### Reading the Data into Bokeh

Here we are transforming our data into a format that is readable by the Bokeh mapper (Column Data Source). To do this the first line of each pair of statements drops the geometry column and assigns the resulting dataframe to a new variable. The second line generates the Column Data Source for use in Bokeh

In [9]:
pt_df = collisions_pt.drop('geometry', axis=1).copy()
pt1_source = ColumnDataSource(pt_df)

ln_df = road_ln.drop('geometry', axis=1).copy()
ln1_source = ColumnDataSource(ln_df)

poly_df = kitchener_poly.drop('geometry', axis=1).copy()
poly1_source = ColumnDataSource(poly_df)

### Selecting our Colour Ramp

This uses the palette that we set at the top with the import statements in order to set our colour ramp for displaying the population data in the map. The first line of code reverses the colour order so that lighter colours are assoicated with less population and darker colours are assoicated with more population. The full set of colour ramps in Bokeh can be found on this website: http://docs.bokeh.org/en/1.3.2/docs/reference/palettes.html, feel free to change the option used in the code, remember that you need to change the import statement first.

In [10]:
palette = Greens8[::-1]
color_mapper = LogColorMapper(palette=palette)

### Generating the Map

This last cell of code generates the map using all of the other components we have explored. It combines the point, line, and polygon geopandas dataframes into one interactive figure that allows you to zoom and identify different points across the City of Kitchener. Note the draw order of the data, we first load the polygon file, then the line file, and last the point file which is reflected in the final map appearance.

In [11]:
# Generating the plot figure
p1 = figure(title="Traffic Collisions in Kitchener, Ontario")

# Plot Kitchener polygon file
da = p1.patches('x', 'y', source=poly1_source,
         fill_color={'field': 'Population_Class_Quantile', 'transform': color_mapper},
         fill_alpha=1.0, line_color="black", line_width=1)

# Add the road network on top of the same figure
road = p1.multi_line('x', 'y', source=ln1_source, color="red", line_width=1)

# Add traffic collisions on top (as yellow points)
collision = p1.circle('x', 'y', size=7, source=pt1_source, color="yellow")

# Creating the hover tools
# Initializes the first hover tool for the traffic collision data
pt_hover = HoverTool(renderers=[collision])
# Adds the tool tips to display the date, light conditions, and weather conditions for each accident
pt_hover.tooltips=[("Date", "@ACCIDENTDA"),
                ("Light Conditions", "@LIGHT"),
                    ("Weather", "@ENVIRONMEN")]

# Initializes the hover tool for the Kitchener DAs
poly_hover = HoverTool(renderers=[da])
# Adds the tools tips to display the DA IDs and the Population of each
poly_hover.tooltips=[("DA ID", "@DAUID"),
                ("Population", "@Population")]

# Adds both tools to the interactive map
p1.add_tools(pt_hover)
p1.add_tools(poly_hover)

# Outputs the map to our jupyter notebook
output_notebook()

# Displays the map within the notebook
show(p1)


Loading BokehJS ...